In [0]:
import queue
import random
import torch
import copy
import os
import sys
import math
import argparse
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import torch.utils.data
from torch import optim
from torch import nn
from torch import distributions as dist
from enum import Enum
import warnings
warnings.filterwarnings('ignore')

Gaussian and BNN Initialisation

In [0]:
# Load device 
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print('Using device: {}'.format(device))

# Mixture parameters for Gaussian
PI = 0.5

SIG_1 = torch.tensor([math.exp(-0)]) # sigma1
SIG_2 = torch.tensor([math.exp(-6)]) # sigma2

# Place tensor in GPU if device is cuda
if torch.cuda.is_available():
  SIG_1 = SIG_1.cuda()
  SIG_2 = SIG_2.cuda()

# Default parameters for Gaussian
Mu_PRI = 0 # mu of prior
SIG_PRI = torch.tensor([math.exp(-0)]) # sigma of prior

# place tensor in GPU if device is cuda
if torch.cuda.is_available():
    SIG_PRI = SIG_PRI.cuda()

# Initial weight hyperparameters
Mu_W = (-0.03, 0.03)
Rho_W = (-8, -7)
Mu_B = (-0.03, 0.03)
Rho_B = (-8, -7)

# Loss variance
SIGMA = torch.tensor([math.exp(-2)])

# place tensor in GPU if device is cuda 
if torch.cuda.is_available():
    SIGMA = SIGMA.cuda()

class PriorType(Enum):
  MIXTURE = 1
  GAUSSIAN = 2

class ActivationType(Enum):
  NONE = 0
  RELU = 1
  SOFTMAX = 2
  TANH = 3
  SIGMOID = 4

class TaskType(Enum):
  REGRESSION = 1
  CLASSIFICATION = 2



Using device: cpu


In [0]:
class GaussianMixture(object):

  def __init__(self, pi, sigma1, sigma2):
    self.pi = pi
    self.sigma1 = sigma1
    self.sigma2 = sigma2

  
  def log_prob(self, weights):
    new_weights = weights.view(-1)
    normal_den1 = dist.Normal(0,self.sigma1).log_prob(new_weights)
    exp_normal_den1 = torch.exp(normal_den1)
    exp_normal_den2 = torch.exp(
        dist.Normal(0.0, self.sigma2).log_prob(new_weights))
    nonzero = exp_normal_den2.nonzero()
    zero = (exp_normal_den2==0).nonzero()
    sum_log_prob = torch.sum(torch.log(self.pi * torch.take(exp_normal_den1,nonzero) \
                  + (1-self.pi)*torch.take(exp_normal_den2,nonzero))) \
                  + torch.sum(torch.take(normal_den1, zero)+np.log(self.pi))
    return sum_log_prob

BNN Definition

In [0]:
class BayesLayer(nn.Module):

  def __init__(self,
               input_size,
               output_size,
               prior_type=PriorType.MIXTURE,
               prior_params={'pi' : PI, 'sigma1' : SIG_1, 'sigma2' : SIG_2},
               activation_type=ActivationType.NONE,
               init_mu_weights=Mu_W,
               init_mu_bias=Mu_B,
               init_rho_weights=Rho_W,
               init_rho_bias=Rho_B
              ):
    super().__init__()
    self.input_size = input_size
    self.output_size = output_size
    self.activation_type = activation_type

    # torch variables
    if not torch.cuda.is_available():
        self.mu_weights = nn.Parameter(torch.Tensor(output_size, input_size))
        self.rho_weights = nn.Parameter(torch.Tensor(output_size, input_size))
        self.mu_bias = nn.Parameter(torch.Tensor(output_size))
        self.rho_bias = nn.Parameter(torch.Tensor(output_size))
        self.normal_dist = dist.Normal(torch.Tensor([0]), torch.Tensor([1]))
    else:
        self.mu_weights = nn.Parameter(torch.Tensor(output_size, input_size).cuda())
        self.rho_weights = nn.Parameter(torch.Tensor(output_size, input_size).cuda())
        self.mu_bias = nn.Parameter(torch.Tensor(output_size).cuda())
        self.rho_bias = nn.Parameter(torch.Tensor(output_size).cuda())
        self.normal_dist = dist.Normal(torch.Tensor([0]).cuda(), torch.Tensor([1]).cuda())

    # initialize variables
    self.mu_weights.data.uniform_(*init_mu_weights)
    self.rho_weights.data.uniform_(*init_rho_weights)
    self.mu_bias.data.uniform_(*init_mu_bias)
    self.rho_bias.data.uniform_(*init_rho_bias)

    if prior_type == PriorType.MIXTURE:
      self.prior_weights = GaussianMixture(
          prior_params['pi'], prior_params['sigma1'], prior_params['sigma2'])
      self.prior_bias = GaussianMixture(
          prior_params['pi'], prior_params['sigma1'], prior_params['sigma2'])
    else:
      self.prior_weights = dist.Normal(prior_params['mean'],
                                       prior_params['sigma'])
      self.prior_bias = dist.Normal(prior_params['mean'],
                                    prior_params['sigma'])
    self.log_prior = 0
    self.log_posterior = 0

  def gaussian_sample(self, mu, rho):
    epsilon = self.normal_dist.sample(rho.size()).squeeze(-1)
    return mu + torch.log(1 + torch.exp(rho)) * epsilon

  def forward(self, input_data, sample=False, debug=False, 
              avg_weights=False, avg_weight_count=2):

    if self.training or sample:
      
       
      # averaging weights
      if avg_weights:
        sum_weights = torch.zeros_like(self.mu_weights)
        sum_bias = torch.zeros_like(self.mu_bias)
        for _ in range(avg_weight_count):
           sum_weights += self.gaussian_sample(
             self.mu_weights, self.rho_weights)
           sum_bias += self.gaussian_sample(
             self.mu_bias, self.rho_bias)
        weights = sum_weights / avg_weight_count
        bias = sum_bias / avg_weight_count
      else:     
        weights = self.gaussian_sample(
          self.mu_weights, self.rho_weights)
        bias = self.gaussian_sample(
          self.mu_bias, self.rho_bias)

      self.log_prior = (self.prior_weights.log_prob(weights).sum() +
                        self.prior_bias.log_prob(bias).sum() )
      sigma_weights = torch.log(1 + torch.exp(self.rho_weights))
      sigma_bias = torch.log(1 + torch.exp(self.rho_bias))
      self.log_posterior = (
          dist.Normal(
              self.mu_weights, sigma_weights).log_prob(weights).sum() +
          dist.Normal(self.mu_bias, sigma_bias).log_prob(bias).sum()
      )

      if torch.isnan(self.log_posterior):
        print('Oops, nan in log_posterior')
        print('log_posterior for weights is {}'.format(dist.Normal(
          self.mu_weights, sigma_weights).log_prob(weights).sum()))
        print('log_posterior for bias is {}'.format(dist.Normal(
          self.mu_bias, sigma_bias).log_prob(bias).sum()))
    else:
      weights = self.mu_weights
      bias = self.mu_bias

    linear_output = nn.functional.linear(input_data, weights, bias)
    output = linear_output
    if self.activation_type == ActivationType.RELU:
      output = torch.relu(linear_output)
    elif self.activation_type == ActivationType.SOFTMAX:
      output = torch.log_softmax(linear_output, dim=1)
    elif self.activation_type == ActivationType.SIGMOID:
      output = torch.sigmoid(linear_output)
    elif self.activation_type == ActivationType.TANH:
      output = torch.tanh(linear_output)
    elif self.activation_type == ActivationType.NONE:
      output = linear_output
    else:
      raise ValueError('activation_type {} not support'.format(self.activation_type))
    return output

  def extra_repr(self):
    return 'Bayes Layer, in_size:{}, out_size:{}, activation_type:{}'.format(
      self.input_size, self.output_size, self.activation_type.name
    )

In [0]:
class BayesNN(nn.Module):

  def __init__(
      self,
      nn_input_size,
      layer_config=[100, 100, 10],           
      activation_config=[ActivationType.RELU, ActivationType.RELU, ActivationType.NONE],
      prior_type=PriorType.MIXTURE,
      prior_params={'pi' : PI, 'sigma1' : SIG_1, 'sigma2' : SIG_2},
      task_type=TaskType.REGRESSION,         
      init_mu_weights=Mu_W,
      init_mu_bias=Mu_B,
      init_rho_weights=Rho_W,
      init_rho_bias=Rho_B
  ):
    super().__init__()

    self.layers = nn.ModuleList([]) 
    self.input_size = nn_input_size
    for i, output_size in enumerate(layer_config):
      if i == 0:
        input_size = self.input_size
      else:
        input_size = layer_config[i-1]

      bayes_layer = BayesLayer(input_size, output_size,
                                     activation_type = activation_config[i],
                                     prior_type=prior_type,
                                     prior_params=prior_params,
                                     init_mu_weights=init_mu_weights,
                                     init_mu_bias=init_mu_bias,
                                     init_rho_weights=init_rho_weights,
                                     init_rho_bias=init_rho_bias)
      self.layers.append(bayes_layer)
    self.output_size = self.layers[-1].output_size
    self.task_type = task_type

  def forward(self, input_data, sample=True, debug=False,
              avg_weights=False, avg_weight_count=2):
    current_data = input_data
    for layer in self.layers:
      current_data = layer.forward(current_data, sample, debug=debug,
                                   avg_weights=avg_weights,
                                   avg_weight_count=avg_weight_count)
    if sample is False:
        print("not sampling.")
    return current_data

  # sample a bunch weights
  # make predictions 
  # output averaged predictions 
  def predict_by_sampling(self, input_data, num_samples=1):

    # reduce the use of buffer
    with torch.no_grad():
        outputs = torch.empty(num_samples, input_data.size()[0], self.output_size)
        for i in range(num_samples):
            
            outputs[i] = self.forward(input_data, sample=True, debug=True)
            
        stds = outputs.std(0)
        outputs = outputs.mean(0)
    return outputs

  def log_prior(self):
    log_prior = 0
    for layer in self.layers:
      log_prior += layer.log_prior
    return log_prior

  def log_posterior(self):
    log_posterior = 0
    for layer in self.layers:
      log_posterior += layer.log_posterior
    return log_posterior

  def cost_function(self, inputs, targets, num_samples, ratio):
    sum_log_posterior = 0
    sum_log_prior = 0
    sum_neg_log_likeli = 0
    for _ in range(num_samples):
      outputs = self(inputs, sample=True)
      sum_log_posterior += self.log_posterior()
      sum_log_prior += self.log_prior()
      if self.task_type == TaskType.CLASSIFICATION:

         # log softmax active function
         log_probs = outputs[range(targets.size()[0]), targets]

         
         
         neg_log_likeli = -log_probs.sum()
      elif self.task_type == TaskType.REGRESSION:
         neg_log_likeli = - dist.Normal(
             targets, SIGMA).log_prob(outputs).sum()
      sum_neg_log_likeli += neg_log_likeli
    kl_divergence = (sum_log_posterior / num_samples - sum_log_prior / num_samples) * ratio
    neg_log_likeli = sum_neg_log_likeli / num_samples
    loss =  kl_divergence + neg_log_likeli
    return loss, kl_divergence, neg_log_likeli

  def extra_repr(self):
    repr = ''
    for layer in self.layers:
      repr += layer.extra_repr()
      repr += '\n'
    return repr

Definition of components in Experiment

In [0]:

SAMPLE_NUM = 2
ACTIONS_NUM = 2
BUFFER = 4096



In [0]:
class Agent(object):  
  def __init__(self):
    # last 4096 interactions with the Mushroom bandit
    self.pre_context = []
    self.pre_action = []
    self.pre_reward = []
    self.value_estimates = None
    
    
  def collect_data(self):
    return len(self.pre_context)

  def select_action(self, context, logs):
    pass
  def variational_posterior_update(self, logs):
    pass
  def update_buffer(self, context, action, reward):
    self.pre_context.append(context)
    self.pre_action.append(action)
    self.pre_reward.append(reward)
    if len(self.pre_context) == BUFFER:
      self.pre_context = self.pre_context[1:]
      self.pre_action = self.pre_action[1:]
      self.pre_reward = self.pre_reward[1:]

In [0]:
class EpsGrAgent(Agent):
  def __init__(self, epsilon, optimizer_constructor=torch.optim.Adam, optim_params={'lr':1e-3, 'eps':0.01}):
    super().__init__()
    self.epsilon = epsilon
    self.value_estimates =  nn.Sequential(
        torch.nn.Linear(118, 100),
        torch.nn.ReLU(),
        torch.nn.Linear(100, 100),
        torch.nn.ReLU(),
        torch.nn.Linear(100, 1),
    )
    
    self.loss_fn = nn.MSELoss()
    
    if torch.cuda.is_available():
      self.value_estimates = self.value_estimates.cuda()

    self.optimizer = optimizer_constructor(self.value_estimates.parameters(), **optim_params)
    
    
  def select_action(self, context, logs=False):
    if random.random() < self.epsilon:
      return random.randint(0,ACTIONS_NUM-1)
    
    max_reward = -36
    argmax_action = -1
    for action in range(ACTIONS_NUM):
      estimated_reward = 0
      
        
      action_tensor = torch.tensor([[action]], dtype=torch.float)
        
      context_and_action = torch.cat(
          [context, action_tensor], dim=1)
        
      if torch.cuda.is_available():
        context_and_action = context_and_action.cuda()
        
      estimated_reward = self.value_estimates(context_and_action)
      if logs:
        print('chosen action {} - estimated reward: {}'.format(
            action, estimated_reward))
      if estimated_reward > max_reward:
        max_reward = estimated_reward
        argmax_action = action
    return argmax_action

  
  def variational_posterior_update(self, logs=False):
    features = []
    for context, action in zip(iter(self.pre_context),
                               iter(self.pre_action)):
      
      action_tensor = torch.tensor([[action]], dtype=torch.float)
      
      features.append(torch.cat(
          [context, action_tensor], dim=1))
    features = torch.cat(features)
    
    rewards = torch.tensor(self.pre_reward, dtype=torch.float)

    pre_set = torch.utils.data.TensorDataset(features, rewards)
    pre_loader = torch.utils.data.DataLoader(
        pre_set, batch_size=64, shuffle=True, num_workers=4)
    
    avg_loss = 0
    
    for i, data in enumerate(pre_loader):
      inputs, labels = data
      if torch.cuda.is_available():
        inputs = inputs.cuda()
        labels = labels.cuda()
      # zero the parameter gradients
      self.optimizer.zero_grad()

      # forward 
      # backward 
      # optimize
      loss = self.loss_fn(self.value_estimates(inputs).squeeze(), labels)

      loss.backward()
      self.optimizer.step()
     
      avg_loss += loss
      
    avg_loss /= len(pre_loader.dataset)
    
    if logs:
      print('Loss: {}'.format(avg_loss))
    return avg_loss    

In [0]:
class AgentBNN(Agent):
  
  def __init__(self, optimizer_constructor=torch.optim.Adam, 
               optim_params={'lr':1e-3, 'eps':0.01},
               prior_params=None,
               lr_scheduler_step_size=32,
               lr_scheduler_gamma=0.1,
               avg_weights=False,
               avg_weights_count=2,
               init_mu_weights=[-0.5, 0.5],
               init_mu_bias=[-0.5, 0.5],
               init_rho_weights=[-4, -2],
               init_rho_bias=[-4, -2]):
        
    super().__init__()
    
    # Estimating[reward | context, action]
    
    bayes_params = {'nn_input_size': 118,
                  'layer_config': [100, 100, 1],
                  'activation_config': [ActivationType.RELU, 
                                        ActivationType.RELU, ActivationType.NONE],
                  'init_mu_weights': init_mu_weights,
                  'init_mu_bias': init_mu_bias,
                  'init_rho_weights': init_rho_weights,
                  'init_rho_bias': init_rho_bias
                 }
    
    if prior_params is not None:
        bayes_params['prior_params'] = prior_params
    
    self.value_estimates = BayesNN(**bayes_params)
        
    if torch.cuda.is_available():
      self.value_estimates = self.value_estimates.cuda()
    
    self.optimizer = optimizer_constructor(
      self.value_estimates.parameters(), **optim_params)
    self.scheduler = torch.optim.lr_scheduler.StepLR(
      self.optimizer, step_size=lr_scheduler_step_size, 
      gamma=lr_scheduler_gamma)

    self.avg_weights = avg_weights
    self.avg_weights_count = avg_weights_count
  

  def select_action(self, context, logs=False):
    self.value_estimates.train()
    max_reward = -36
    argmax_action = -1
    for action in range(ACTIONS_NUM):
      expected_reward = 0
      if self.avg_weights:
        sample_count = 1
      else:
        sample_count = SAMPLE_NUM
      for i in range(sample_count):
        
        action_tensor = torch.tensor([[action]], dtype=torch.float)
        
        context_and_action = torch.cat(
            [context, action_tensor], dim=1)
        
        if torch.cuda.is_available():
          context_and_action = context_and_action.cuda()
        
        expected_reward += self.value_estimates(
          context_and_action, avg_weights=self.avg_weights,
          avg_weight_count=self.avg_weights_count)
      expected_reward /= sample_count
      if logs:
        print('chosen action {} - estimated reward: {}'.format(
            action, expected_reward))
      if expected_reward > max_reward:
        max_reward = expected_reward
        argmax_action = action
    return argmax_action
  

  def variational_posterior_update(self, logs=False):
    features = []
    for context, action in zip(iter(self.pre_context),
                               iter(self.pre_action)):
      
      action_tensor = torch.tensor([[action]], dtype=torch.float)
      
      features.append(torch.cat(
          [context, action_tensor], dim=1))
    features = torch.cat(features)
    
    rewards = torch.tensor(self.pre_reward, dtype=torch.float)

    pre_set = torch.utils.data.TensorDataset(features, rewards)
    pre_loader = torch.utils.data.DataLoader(
        pre_set, batch_size=64, shuffle=True, num_workers=4)
    
    avg_loss = 0
    avg_kl_divergence = 0
    avg_nll = 0
    
    for i, data in enumerate(pre_loader):
      inputs, labels = data
      if torch.cuda.is_available():
        inputs = inputs.cuda()
        labels = labels.cuda()

      # zero gradients parameter 
      self.optimizer.zero_grad()

      # forward 
      # backward 
      # optimize
      loss, kl_divergence, nll = self.value_estimates.cost_function(
          inputs, labels, num_samples=2, ratio=1/len(pre_loader))
      loss.backward()
      self.optimizer.step()
      torch.nn.utils.clip_grad_norm_(self.value_estimates.parameters(),
                                     4)
     
      avg_loss += loss
      avg_kl_divergence += kl_divergence
      avg_nll += nll
      
    dataset_len = len(pre_loader.dataset)  
    avg_loss /= dataset_len
    avg_kl_divergence /= dataset_len
    avg_nll /= dataset_len
    self.scheduler.step()
    
    if logs:
      print('Loss: {}'.format(avg_loss))
      print('Kullback div: {}'.format(avg_kl_divergence))
    return avg_loss.item(), avg_kl_divergence.item(), avg_nll.item()

In [0]:
class Environment(object):
  
  def __init__(self, agent, dataloader, name):
    self.agent = agent
    self.dataloader = dataloader
    self.name = name
    self.cumulative_regret = 0
  
  def play_round(self, logs=False):
    
    # Get the contexts
    #label random mushroom
    context, mush_type = next(iter(self.dataloader))
    
    if torch.cuda.is_available():
      mush_type = mush_type.cuda()
    
    # Reward defenition 
    if mush_type == 1:
      eat_reward = 5
      oracle_reward = 5
      mush_string = 'Edible'
    else: 
      oracle_reward = 0
      mush_string = 'Poisonous'
      random_draw = random.random()
      if random_draw > 0.5:
        eat_reward = 5
      else:
        eat_reward = -35
        
    # selecting action in repect of context
    selected_action = self.agent.select_action(context, logs)
    
    # Reward of Action
    if selected_action == 0: #pass
      action_string = 'passing'
      reward = 0
    else: #eat
      action_string = 'eating'
      reward = eat_reward


    # Cumulative Regret
    self.cumulative_regret += max(oracle_reward - reward, 0) 
    
    if logs:
      print('{} mushroom. Agent select {}. Received a reward: {}.'.format(mush_string, action_string, reward))
      print('Cumulative sum of regret {}'.format(self.cumulative_regret))
      
    # Send reward back to the agent
    self.agent.update_buffer(context, selected_action, reward)

    
    update_results = self.agent.variational_posterior_update(logs)
    
    return update_results

Our Experiment

In [0]:
def read_args(args=None):
  parser = argparse.ArgumentParser()
  parser.add_argument('--optimizer_type', type=str, default='SGD')
  parser.add_argument('--eps_learning_rate', type=float, default=1e-3)
  parser.add_argument('--eps_epsilon', type=float, default=1e-3)
  parser.add_argument('--eps_momentum', type=float, default=0)
  parser.add_argument('--bayes_learning_rate', type=float, default=2e-7)
  parser.add_argument('--bayes_epsilon', type=float, default=1e-3)
  parser.add_argument('--bayes_momentum', type=float, default=0)
  parser.add_argument('--bayes_lr_scheduler_step_size', type=int, default=10000)
  parser.add_argument('--bayes_lr_scheduler_gamma', type=float, default=0.1)
  parser.add_argument('--bayes_pi', type=float, default=0.5 )
  parser.add_argument('--bayes_log_sigma1', type=float, default=math.exp(-3))
  parser.add_argument('--bayes_log_sigma2', type=float, default=math.exp(-8))
  parser.add_argument('--avg_weights', dest='avg_weights', action='store_true')
  parser.add_argument('--avg_weights_count', type=int, default=2)
  parser.add_argument('--init_mu_weights_range', type=float, nargs=2, default=[-0.05, 0.05])
  parser.add_argument('--init_mu_bias_range', type=float, nargs=2, default=[-0.05, 0.05])
  parser.add_argument('--init_rho_weights_range', type=float, nargs=2, default=[-7, -6])
  parser.add_argument('--init_rho_bias_range', type=float, nargs=2, default=[-7, -6])
  parser.add_argument('--number_of_runs', type=int, default=4)
  args = parser.parse_args(args=[])
  return args


if __name__ == '__main__':

  mush_dataset = pd.read_csv('mushrooms.csv')
  train_labels = mush_dataset['class']
  train_labels = train_labels.replace(['p', 'e'],
                                [-1, 1])
  train_features = pd.get_dummies(mush_dataset.drop(['class'], axis=1))

  train_features = torch.tensor(train_features.values, dtype=torch.float)
  train_labels = torch.tensor(train_labels.values)

  trainset = torch.utils.data.TensorDataset(train_features, train_labels)
  trainloader = torch.utils.data.DataLoader(trainset, batch_size=1,
                                            shuffle=True, num_workers=0)
    
	# Parameters for bayesNN and epsilon greedy agents
  args = read_args(sys.argv)
  
  if args.optimizer_type == 'Adam':
    optimizer_constructor = torch.optim.Adam
    epsg_optimizer_params = {'lr': args.eps_learning_rate,
                           'eps': args.eps_epsilon}
    bayes_optimizer_params = {'lr': args.bayes_learning_rate,
                            'eps': args.bayes_epsilon}
  elif args.optimizer_type == 'SGD':
    optimizer_constructor = torch.optim.SGD
    eps_optimizer_params = {'lr': args.eps_learning_rate,
                           'momentum': args.eps_momentum}
    bayes_optimizer_params = {'lr': args.bayes_learning_rate, 
                            'momentum': args.bayes_momentum}
  
  sigma1 = math.exp(args.bayes_log_sigma1)
  sigma2 = math.exp(args.bayes_log_sigma2)
  prior_params = {'pi': args.bayes_pi, 
                  'sigma1': sigma1,
                  'sigma2': sigma2}

  bayes_envs = []
  eps5_envs = []
  eps1_envs = []
  eps0_envs = []
  envs = []

  for j in range(args.number_of_runs):

    bayes_agent = AgentBNN(optimizer_constructor=optimizer_constructor,
                  optim_params=bayes_optimizer_params,
                  prior_params=prior_params,
                  lr_scheduler_step_size=args.bayes_lr_scheduler_step_size,
                  lr_scheduler_gamma=args.bayes_lr_scheduler_gamma,
                  avg_weights=args.avg_weights,
                  avg_weights_count=args.avg_weights_count,
                  init_mu_weights=args.init_mu_weights_range,
                  init_mu_bias=args.init_mu_bias_range,
                  init_rho_weights=args.init_rho_weights_range,
                  init_rho_bias=args.init_rho_bias_range)
    bayes_env = Environment(bayes_agent, trainloader,
                          'Bayes by Backprop')

    eps5_agent = EpsGrAgent(epsilon=.05, 
                        optimizer_constructor=optimizer_constructor,
                        optim_params=eps_optimizer_params)
    eps5_env = Environment(eps5_agent, copy.deepcopy(trainloader),
                          '5% Ɛ-Greedy')

    eps1_agent = EpsGrAgent(epsilon=.01, 
                        optimizer_constructor=optimizer_constructor,
                        optim_params=eps_optimizer_params)
    eps1_env = Environment(eps1_agent, copy.deepcopy(trainloader),
                          '1% Ɛ-Greedy')

    eps0_agent = EpsGrAgent(epsilon=.00, 
                        optimizer_constructor=optimizer_constructor,
                        optim_params=eps_optimizer_params)
    eps0_env = Environment(eps0_agent, copy.deepcopy(trainloader),
                          'Greedy')

    bayes_envs.append(bayes_env)
    eps5_envs.append(eps5_env)
    eps1_envs.append(eps1_env)
    eps0_envs.append(eps0_env)


  bayes_loss = []
  bayes_kl_divergence = []
  bayes_nll = []




  eps5_regret = []
  eps1_regret = []
  eps0_regret = []
  bayes_regret = []


  envs = [(eps5_envs, eps5_regret),
          (eps1_envs, eps1_regret),
          (eps0_envs, eps0_regret),
          (bayes_envs, bayes_regret)]

 

  for step in range(20000):

    logs = False

    if (step+1) % 100 == 0:
      logs = True
      print('Step {}'.format(step))

    for env_set, regret in envs:
      if logs:
        print(env_set[0].name)
      is_bnn = env_set[0].name == 'Bayes by Backprop'
      avg_regret = 0
     
      if is_bnn:
        avg_loss = 0
        avg_kl_divergence = 0
        avg_nll = 0
      for env in env_set:
        if is_bnn:
          loss, kl_divergence, nll = env.play_round(logs=logs)
        else:
          env.play_round(logs=logs)
        avg_regret += env.cumulative_regret
        
        if is_bnn:
          avg_loss += loss
          avg_kl_divergence += kl_divergence
          avg_nll += nll
      avg_regret /= args.number_of_runs
      
      if is_bnn:
        avg_loss /= args.number_of_runs
        avg_kl_divergence /= args.number_of_runs
        avg_nll /= args.number_of_runs 
        bayes_loss.append(avg_loss)
        bayes_kl_divergence.append(avg_kl_divergence)
        bayes_nll.append(avg_nll)
      regret.append(avg_regret)
    
    if (step+1) % 200 == 0:
      
      for env_set, regret in envs:
        plt.plot(np.array(regret), label=env_set[0].name)
      plt.legend()
      plt.title('Cumulative regret of various agents on the mushroom bandit task')
      plt.ylabel('Cumulative Regret')
      plt.xlabel('Steps')
      plt.savefig('reg_{}'.format(step+1), dpi=400, bbox_inches='tight')
      plt.clf()

Step 99
5% Ɛ-Greedy
chosen action 0 - estimated reward: tensor([[-1.0763]], grad_fn=<AddmmBackward>)
chosen action 1 - estimated reward: tensor([[-1.1547]], grad_fn=<AddmmBackward>)
Edible mushroom. Agent select passing. Received a reward: 0.
Cumulative sum of regret 345
Loss: 1.0218138694763184
chosen action 0 - estimated reward: tensor([[-0.2516]], grad_fn=<AddmmBackward>)
chosen action 1 - estimated reward: tensor([[-0.6768]], grad_fn=<AddmmBackward>)
Edible mushroom. Agent select passing. Received a reward: 0.
Cumulative sum of regret 505
Loss: 2.2900586128234863
chosen action 0 - estimated reward: tensor([[-0.3894]], grad_fn=<AddmmBackward>)
chosen action 1 - estimated reward: tensor([[-0.4443]], grad_fn=<AddmmBackward>)
Edible mushroom. Agent select passing. Received a reward: 0.
Cumulative sum of regret 285
Loss: 0.33119356632232666
chosen action 0 - estimated reward: tensor([[0.0234]], grad_fn=<AddmmBackward>)
chosen action 1 - estimated reward: tensor([[-0.0148]], grad_fn=<Add

Streaming output truncated to the last 5000 lines.
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ign

Step 1199
5% Ɛ-Greedy
chosen action 0 - estimated reward: tensor([[-0.7425]], grad_fn=<AddmmBackward>)
chosen action 1 - estimated reward: tensor([[6.5606]], grad_fn=<AddmmBackward>)
Edible mushroom. Agent select eating. Received a reward: 5.
Cumulative sum of regret 2975


Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable


Loss: 0.04215521737933159
chosen action 0 - estimated reward: tensor([[0.2770]], grad_fn=<AddmmBackward>)
chosen action 1 - estimated reward: tensor([[-22.7600]], grad_fn=<AddmmBackward>)
Poisonous mushroom. Agent select passing. Received a reward: 0.
Cumulative sum of regret 2935


...

Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable


Loss: 52489.29296875
Kullback div: 45.945621490478516
chosen action 0 - estimated reward: tensor([[1.0250]], grad_fn=<DivBackward0>)
chosen action 1 - estimated reward: tensor([[0.7117]], grad_fn=<DivBackward0>)
Poisonous mushroom. Agent select passing. Received a reward: 0.
Cumulative sum of regret 5120


Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable


Loss: 64230.8046875
Kullback div: 45.921348571777344


Streaming output truncated to the last 5000 lines.
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ignored when trying to write to the signal wakeup fd:
BlockingIOError: [Errno 11] Resource temporarily unavailable
Exception ign